In [5]:
import netgen.gui
from ngsolve import *
from netgen.csg import *
from math import pi
from netgen.geom2d import unit_square

mesh = Mesh(unit_square.GenerateMesh(maxh=0.5))

SetNumThreads(4)

#exact u
u1=sin(pi*x)*sin(pi*y)-4/pi**2
u2=cos(pi*x)*cos(pi*y)
uexact = CoefficientFunction((u1, u2))
#exact p
pexact = sin(pi*x)*cos(pi*y)

graduexact = CoefficientFunction((u1.Diff(x), u1.Diff(y), \
                                  u2.Diff(x), u2.Diff(y)), dims=(2,2))
gradpex = CoefficientFunction( (pexact.Diff(x), pexact.Diff(y)) )

#source f
source = CoefficientFunction( (-(graduexact[0,0].Diff(x) + graduexact[0,1].Diff(y)) + gradpex[0], -(graduexact[1,0].Diff(x) + graduexact[1,1].Diff(y)) + gradpex[1]) )

k = 2
V = VectorH1(mesh,order=k)
Q = H1(mesh,order=k-1)
R = NumberSpace(mesh) 
X = FESpace([V, Q, R, R])

gfu = GridFunction(X)

(u,p, lam1, lam2), (v,q, mu1, mu2) = X.TnT()
lam = CoefficientFunction((lam1, lam2))
mu = CoefficientFunction((mu1, mu2))

n = specialcf.normal(mesh.dim)


I = Id(2)
g = (-graduexact + pexact * I)

a = BilinearForm(X, symmetric=True)
a += (InnerProduct(grad(u),grad(v))-div(v)*p-div(u)*q)*dx
a += (lam*v+mu*u) * dx 

f = LinearForm(X)
f += source*v*dx
f += - InnerProduct(g*n,v)*ds(definedon=mesh.Boundaries("top|bottom|left|right"))

res = f.vec.CreateVector()

with TaskManager():
    a.Assemble()
    f.Assemble()
    inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")

    res.data = f.vec - a.mat*gfu.vec
    gfu.vec.data += inv * res

#Solve Stokes function
gfu = GridFunction(X)

output = []
def SolveStokes():
    X.Update()
    gfu.Update()

    with TaskManager():
        #Linear forms
        a.Assemble()
        f.Assemble()
        
        # Solve
        inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
        res = f.vec.CreateVector()
        res.data = f.vec - a.mat*gfu.vec
        gfu.vec.data += inv * res

    velocity = gfu.components[0]
    Draw(velocity,mesh,"u")
    pressure = gfu.components[1]
    Draw(pressure,mesh,"p")

    #error
    u,p,lam1,lam2=gfu.components
    err_u =  sqrt (Integrate ((u-uexact)**2, mesh))
    err_p =  sqrt (Integrate ((p-pexact)**2, mesh))
    output.append ((X.ndof, err_u,err_p))
    print(output)
    return u

uh=SolveStokes()
print("uh",uh)

I = Id(2)
K = uh*uh.trans()/(uh*uh)
Z = I + K


[(52, 0.01937189847217173, 0.058404266487023716)]
uh gridfunction 'gfu.1' on space 'CompoundFESpaces'
nested = 0



NgException: Transpose of non-matrix called